### Multi-Label Classification Using Catboost
---
This is the third iteration for the solution of the Kaggle competition.

Things to cover this time around:
- Feature Creation
- Scaling
- PCA with gridsearch
- Catboost Classifier Optuna
- XGB and LGB options
- Test New features only then with pca, then with optuna.

In [13]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import sklearn as sk
import numpy as np
import catboost as cb
import optuna
import lightgbm as lgb


from scipy.stats import zscore
from sklearn.model_selection import train_test_split
from sklearn.model_selection import StratifiedKFold
from catboost import CatBoostClassifier
from sklearn.metrics import roc_auc_score
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV

C:\Users\logan\anaconda3\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  _numeric_index_types = (pd.Int64Index, pd.Float64Index, pd.UInt64Index)
C:\Users\logan\anaconda3\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.Float64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  _numeric_index_types = (pd.Int64Index, pd.Float64Index, pd.UInt64Index)
C:\Users\logan\anaconda3\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.UInt64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  _numeric_index_types = (pd.Int64Index, pd.Float64Index, pd.UInt64Index)


In [2]:
test = pd.read_csv(r'C:\Users\logan\Desktop\Multi-Label Classification with an Enzyme Substrate Dataset\test.csv')
train = pd.read_csv(r'C:\Users\logan\Desktop\Multi-Label Classification with an Enzyme Substrate Dataset\train.csv')

# Dropping id
test_noid = test.drop('id', axis=1)
train_noid = train.drop('id',axis=1)




In [3]:
# Feature Creating
def divide_with_check(a,b):
    result = np.where(b != 0, np.divide(a, b), 0)
    return result

train_noid['Enzyme_Complexity'] = train_noid['Chi1'] + train_noid['Chi2v'] + train_noid['Chi3v'] + train_noid['Chi4n']
train_noid['Molecular_Weight_Ratio'] = divide_with_check(train_noid['ExactMolWt'], train_noid['HeavyAtomMolWt'])
train_noid['EState_VSA_Ratio'] = divide_with_check(train_noid['EState_VSA1'], train_noid['EState_VSA2'])
train_noid['Heteroatom_Proportion'] = divide_with_check(train_noid['NumHeteroatoms'], (train_noid['NumHeteroatoms'] + train_noid['HeavyAtomMolWt']))
train_noid['frCOO_Average'] = (train_noid['fr_COO'] + train_noid['fr_COO2']) / 2

train_noid['Molecular_Complexity'] = train_noid['BertzCT'] * train_noid['ExactMolWt']
train_noid['Structural_Flexibility'] = train_noid['Chi1'] * train_noid['Chi2n']
train_noid['Functional_Specificity'] = train_noid['Chi1n'] * train_noid['Chi3v']
train_noid['Size_Related_Descriptors'] = train_noid['ExactMolWt'] * train_noid['FpDensityMorgan1']
train_noid['Topological_Patterns'] = train_noid['FpDensityMorgan2'] * train_noid['FpDensityMorgan3']
train_noid['Electronic_Structure'] = train_noid['HallKierAlpha'] * train_noid['MaxAbsEStateIndex']
train_noid['Atom_Weight_and_Charge'] = train_noid['HeavyAtomMolWt'] * train_noid['MinEStateIndex']
train_noid['Geometrical_Shape'] = train_noid['Kappa3'] * train_noid['NumHeteroatoms']
train_noid['Molecular_Surface_Properties'] = train_noid['PEOE_VSA10'] * train_noid['PEOE_VSA14']

train_noid['Chemical_Diversity'] = divide_with_check(train_noid['EState_VSA1'], train_noid['NumHeteroatoms'])
train_noid['Functional_Group_Diversity'] = train_noid['PEOE_VSA6'] * train_noid['PEOE_VSA7']
train_noid['Molecular_Size'] = train_noid['ExactMolWt'] + train_noid['HeavyAtomMolWt']
train_noid['Electronegativity_Difference'] = train_noid['MaxAbsEStateIndex'] - train_noid['MinEStateIndex']
train_noid['Ring_Density'] = divide_with_check(train_noid['NumHeteroatoms'], train_noid['SlogP_VSA3'])
train_noid['Steric_Effects'] = divide_with_check(train_noid['SMR_VSA5'], train_noid['SMR_VSA10'])
train_noid['Hydrophilic_Surface'] = train_noid['VSA_EState9'] * train_noid['EState_VSA2']
train_noid['Molecular_Polarity'] = divide_with_check(train_noid['PEOE_VSA8'], train_noid['EState_VSA1'])

train_noid['Ring_System_Diversity'] = divide_with_check(train_noid['fr_COO'], train_noid['fr_COO2'])
train_noid['Molecular_Flexibility'] = train_noid['Chi2n'] * train_noid['Chi3v']
train_noid['Electrostatic_Potential'] = train_noid['EState_VSA1'] - train_noid['EState_VSA2']
train_noid['Hydrophobicity_Index'] = divide_with_check(train_noid['SMR_VSA10'], train_noid['SMR_VSA5'])
train_noid['Molecular_Conformation'] = train_noid['Chi1'] + train_noid['Chi4n'] - train_noid['Chi2n']
train_noid['Functional_Group_Connectivity'] = train_noid['PEOE_VSA14'] * train_noid['PEOE_VSA10']
train_noid['Steric_Bulkiness'] = train_noid['PEOE_VSA7'] - train_noid['PEOE_VSA6']
train_noid['Aromaticity'] = train_noid['FpDensityMorgan1'] + train_noid['FpDensityMorgan2'] + train_noid['FpDensityMorgan3']
train_noid['Hydrogen_Bonding_Potential'] = train_noid['EState_VSA1'] * train_noid['NumHeteroatoms']
train_noid['Molecular_Polarizability'] = divide_with_check(train_noid['HallKierAlpha'], train_noid['Chi2v'])


In [4]:
test_noid['Enzyme_Complexity'] = test_noid['Chi1'] + test_noid['Chi2v'] + test_noid['Chi3v'] + test_noid['Chi4n']
test_noid['Molecular_Weight_Ratio'] = divide_with_check(test_noid['ExactMolWt'], test_noid['HeavyAtomMolWt'])
test_noid['EState_VSA_Ratio'] = divide_with_check(test_noid['EState_VSA1'], test_noid['EState_VSA2'])
test_noid['Heteroatom_Proportion'] = divide_with_check(test_noid['NumHeteroatoms'], (test_noid['NumHeteroatoms'] + test_noid['HeavyAtomMolWt']))
test_noid['frCOO_Average'] = (test_noid['fr_COO'] + test_noid['fr_COO2']) / 2

test_noid['Molecular_Complexity'] = test_noid['BertzCT'] * test_noid['ExactMolWt']
test_noid['Structural_Flexibility'] = test_noid['Chi1'] * test_noid['Chi2n']
test_noid['Functional_Specificity'] = test_noid['Chi1n'] * test_noid['Chi3v']
test_noid['Size_Related_Descriptors'] = test_noid['ExactMolWt'] * test_noid['FpDensityMorgan1']
test_noid['Topological_Patterns'] = test_noid['FpDensityMorgan2'] * test_noid['FpDensityMorgan3']
test_noid['Electronic_Structure'] = test_noid['HallKierAlpha'] * test_noid['MaxAbsEStateIndex']
test_noid['Atom_Weight_and_Charge'] = test_noid['HeavyAtomMolWt'] * test_noid['MinEStateIndex']
test_noid['Geometrical_Shape'] = test_noid['Kappa3'] * test_noid['NumHeteroatoms']
test_noid['Molecular_Surface_Properties'] = test_noid['PEOE_VSA10'] * test_noid['PEOE_VSA14']

test_noid['Chemical_Diversity'] = divide_with_check(test_noid['EState_VSA1'], test_noid['NumHeteroatoms'])
test_noid['Functional_Group_Diversity'] = test_noid['PEOE_VSA6'] * test_noid['PEOE_VSA7']
test_noid['Molecular_Size'] = test_noid['ExactMolWt'] + test_noid['HeavyAtomMolWt']
test_noid['Electronegativity_Difference'] = test_noid['MaxAbsEStateIndex'] - test_noid['MinEStateIndex']
test_noid['Ring_Density'] = divide_with_check(test_noid['NumHeteroatoms'], test_noid['SlogP_VSA3'])
test_noid['Steric_Effects'] = divide_with_check(test_noid['SMR_VSA5'], test_noid['SMR_VSA10'])
test_noid['Hydrophilic_Surface'] = test_noid['VSA_EState9'] * test_noid['EState_VSA2']
test_noid['Molecular_Polarity'] = divide_with_check(test_noid['PEOE_VSA8'], test_noid['EState_VSA1'])

test_noid['Ring_System_Diversity'] = divide_with_check(test_noid['fr_COO'], test_noid['fr_COO2'])
test_noid['Molecular_Flexibility'] = test_noid['Chi2n'] * test_noid['Chi3v']
test_noid['Electrostatic_Potential'] = test_noid['EState_VSA1'] - test_noid['EState_VSA2']
test_noid['Hydrophobicity_Index'] = divide_with_check(test_noid['SMR_VSA10'], test_noid['SMR_VSA5'])
test_noid['Molecular_Conformation'] = test_noid['Chi1'] + test_noid['Chi4n'] - test_noid['Chi2n']
test_noid['Functional_Group_Connectivity'] = test_noid['PEOE_VSA14'] * test_noid['PEOE_VSA10']
test_noid['Steric_Bulkiness'] = test_noid['PEOE_VSA7'] - test_noid['PEOE_VSA6']
test_noid['Aromaticity'] = test_noid['FpDensityMorgan1'] + test_noid['FpDensityMorgan2'] + test_noid['FpDensityMorgan3']
test_noid['Hydrogen_Bonding_Potential'] = test_noid['EState_VSA1'] * test_noid['NumHeteroatoms']
test_noid['Molecular_Polarizability'] = divide_with_check(test_noid['HallKierAlpha'], test_noid['Chi2v'])


In [5]:
forec1 = train_noid.copy()
forec2 = train_noid.copy()

tforec1 = forec1.drop(['EC2','EC3','EC4','EC5','EC6'], axis=1)
tforec2 = forec2.drop(['EC1','EC3','EC4','EC5','EC6'], axis=1)

X = tforec1.drop('EC1', axis=1)
y = tforec1['EC1']

X1 = tforec2.drop('EC2', axis=1)
y1 = tforec2['EC2']


In [6]:
# Scaling
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)
X1_scaled = scaler.fit_transform(X1)
test_scaled = scaler. fit_transform(test_noid)

In [7]:
# Grid search for PCA using past catboost params
params1 = {'iterations': 162, 'task_type': 'GPU', 'scale_pos_weight': 0.49,'learning_rate': 0.021176655346253584, 
           'depth': 6, 'l2_leaf_reg': 3.362391546879058, 'border_count': 187, 'verbose': 0,
           'bagging_temperature': 0.2531663408352402, 'random_strength': 0.8864625806619271}

params2 = {'iterations': 118, 'task_type': 'GPU', 'scale_pos_weight': 0.25,'learning_rate': 0.0644728408668585,
           'depth': 2, 'l2_leaf_reg': 7.289799901271414, 'verbose':0,
           'border_count': 139, 'bagging_temperature': 0.1873006640760348, 'random_strength': 0.18535510816296885}



pipeline = Pipeline([
    ('pca', PCA()),
    ('classifier', cb.CatBoostClassifier(**params1))])

# Define the parameter grid
param_grid = {
    'pca__n_components': [2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,14 ,15] 
}

# Define the GridSearchCV with cross-validation and scoring metric
grid_search = GridSearchCV(
    estimator=pipeline,
    param_grid=param_grid,
    scoring='roc_auc',
    cv=5
)

# Fit the GridSearchCV
grid_search.fit(X_scaled, y)

# Get the best hyperparameters and score
best_params_ec1 = grid_search.best_params_
best_score_ec1 = grid_search.best_score_

# Retrieve the best model from GridSearchCV
best_model_ec1 = grid_search.best_estimator_

In [8]:
print(best_params_ec1)
print(best_score_ec1)

{'pca__n_components': 6}
0.6980201010131906


In [9]:
pipeline1 = Pipeline([
    ('pca', PCA()),
    ('classifier', cb.CatBoostClassifier(**params2))])

# Define the parameter grid
param_grid = {
    'pca__n_components': [ 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15]  # Adjust the values as per your needs
}

# Define the GridSearchCV with cross-validation and scoring metric
grid_search = GridSearchCV(
    estimator=pipeline1,
    param_grid=param_grid,
    scoring='roc_auc',
    cv=5
)

# Fit the GridSearchCV
grid_search.fit(X1_scaled, y1)

# Get the best hyperparameters and score
best_params_ec2 = grid_search.best_params_
best_score_ec2 = grid_search.best_score_

# Retrieve the best model from GridSearchCV
best_model_ec2 = grid_search.best_estimator_

In [10]:
print(best_params_ec2)
print(best_score_ec2)

{'pca__n_components': 11}
0.5813258961936798


In [11]:
y_pred_ec1 = best_model_ec1.predict(test_scaled)
y_pred_ec2 = best_model_ec2.predict(test_scaled)

In [12]:
submission_pca = pd.DataFrame({'id': test['id'], 'EC1': y_pred_ec1, 'EC2': y_pred_ec2})
submission_pca.to_csv('submission_FC_PCA.csv', index=False)

In [14]:
# Trying LightGBM and PCA first
# Apply PCA to test_scaled before predicting for each target then try optuna again
test_ec1 = test_scaled.copy()
test_ec2 = test_scaled.copy()

pca1 = PCA(n_components=6)
X_pca1 = pca1.fit_transform(X_scaled)
test_pca1 = pca1.fit_transform(test_ec1)

pca2 = PCA(n_components=11)
X_pca2 = pca2.fit_transform(X1_scaled)
test_pca2 = pca2.fit_transform(test_ec2)

In [17]:
# Optuna EC1

def objective(trial):
    # Define the hyperparameters to optimize
    params = {
        'objective': 'binary',
        'metric': 'auc',
        'boosting_type': 'gbdt',
        'num_leaves': trial.suggest_int('num_leaves', 10, 200),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1),
        'feature_fraction': trial.suggest_float('feature_fraction', 0.1, 1.0),
        'bagging_fraction': trial.suggest_float('bagging_fraction', 0.1, 1.0),
        'bagging_freq': trial.suggest_int('bagging_freq', 1, 10),
        'min_child_samples': trial.suggest_int('min_child_samples', 1, 100),
        'lambda_l1': trial.suggest_float('lambda_l1', 1e-8, 10.0),
        'lambda_l2': trial.suggest_float('lambda_l2', 1e-8, 10.0),
        'seed': 42
    }

    # Perform cross-validation with StratifiedKFold
    cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
    scores = []
    for train_idx, val_idx in cv.split(X_pca1, y):
        X_train, X_val = X_pca1[train_idx], X_pca1[val_idx]
        y_train, y_val = y.iloc[train_idx], y.iloc[val_idx]

        train_data = lgb.Dataset(X_train, label=y_train)
        val_data = lgb.Dataset(X_val, label=y_val)

        model = lgb.train(params, train_data, valid_sets=[train_data, val_data],
                          num_boost_round=1000, early_stopping_rounds=50, verbose_eval=False)

        y_pred = model.predict(X_val)
        score = roc_auc_score(y_val, y_pred)
        scores.append(score)

    # Return the mean score as the objective value for Optuna
    return np.mean(scores)


In [18]:
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=100)


[I 2023-07-07 09:50:17,652] A new study created in memory with name: no-name-231bb770-50b6-466c-9959-55e6305b2aba
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "


[LightGBM] [Info] Number of positive: 7926, number of negative: 3944
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000078 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1530
[LightGBM] [Info] Number of data points in the train set: 11870, number of used features: 6
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.667734 -> initscore=0.697953
[LightGBM] [Info] Start training from score 0.697953
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain:

C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argum

[LightGBM] [Info] Number of positive: 7926, number of negative: 3944
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000186 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1530
[LightGBM] [Info] Number of data points in the train set: 11870, number of used features: 6
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.667734 -> initscore=0.697953
[LightGBM] [Info] Start training from score 0.697953
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

...

[LightGBM] [Info] Number of positive: 7926, number of negative: 3944
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000248 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1530
[LightGBM] [Info] Number of data points in the train set: 11870, number of used features: 6
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.667734 -> initscore=0.697953
[LightGBM] [Info] Start training from score 0.697953


C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "


[LightGBM] [Info] Number of positive: 7926, number of negative: 3944
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001599 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1530
[LightGBM] [Info] Number of data points in the train set: 11870, number of used features: 6
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.667734 -> initscore=0.697953
[LightGBM] [Info] Start training from score 0.697953
[LightGBM] [Info] Number of positive: 7927, number of negative: 3944
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000215 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1530
[LightGBM] [Info] Number of data points in the train set: 11871, number of used features: 6
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.667762 -> initscore=0.698079
[LightGBM] [Info] Start training from score 0.698079


C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "
[I 2023-07-07 09:51:50,435] Trial 99 finished with value: 0.6969263740155258 and parameters: {'num_leaves': 32, 'learning_rate': 0.0513339487242574, 'feature_fraction': 0.9325645525667074, 'bagging_fraction': 0.8068137797668969, 'bagging_freq': 4, 'min

[LightGBM] [Info] Number of positive: 7927, number of negative: 3944
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000213 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1530
[LightGBM] [Info] Number of data points in the train set: 11871, number of used features: 6
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.667762 -> initscore=0.698079
[LightGBM] [Info] Start training from score 0.698079


In [19]:
best_params1 = study.best_params
best_score1 = study.best_value

print(best_params1)
print(best_score1)

{'num_leaves': 11, 'learning_rate': 0.05077249353326805, 'feature_fraction': 0.958792442194968, 'bagging_fraction': 0.6562877171636153, 'bagging_freq': 4, 'min_child_samples': 32, 'lambda_l1': 0.09118756023940255, 'lambda_l2': 8.567934907371729}
0.6993270326942582


In [20]:
def objective1(trial):
    # Define the hyperparameters to optimize
    params = {
        'objective': 'binary',
        'metric': 'auc',
        'boosting_type': 'gbdt',
        'num_leaves': trial.suggest_int('num_leaves', 10, 200),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1),
        'feature_fraction': trial.suggest_float('feature_fraction', 0.1, 1.0),
        'bagging_fraction': trial.suggest_float('bagging_fraction', 0.1, 1.0),
        'bagging_freq': trial.suggest_int('bagging_freq', 1, 10),
        'min_child_samples': trial.suggest_int('min_child_samples', 1, 100),
        'lambda_l1': trial.suggest_float('lambda_l1', 1e-8, 10.0),
        'lambda_l2': trial.suggest_float('lambda_l2', 1e-8, 10.0),
        'seed': 42
    }

    # Perform cross-validation with StratifiedKFold
    cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
    scores = []
    for train_idx, val_idx in cv.split(X_pca2, y1):
        X_train, X_val = X_pca2[train_idx], X_pca2[val_idx]
        y_train, y_val = y1.iloc[train_idx], y1.iloc[val_idx]

        train_data = lgb.Dataset(X_train, label=y_train)
        val_data = lgb.Dataset(X_val, label=y_val)

        model = lgb.train(params, train_data, valid_sets=[train_data, val_data],
                          num_boost_round=1000, early_stopping_rounds=50, verbose_eval=False)

        y_pred = model.predict(X_val)
        score = roc_auc_score(y_val, y_pred)
        scores.append(score)

    # Return the mean score as the objective value for Optuna
    return np.mean(scores)


In [21]:
study1 = optuna.create_study(direction='maximize')
study1.optimize(objective1, n_trials=100)

[I 2023-07-07 09:54:19,681] A new study created in memory with name: no-name-ac0c8ad9-0dcd-4e1e-92a3-f030de68ca8a
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "


[LightGBM] [Info] Number of positive: 9484, number of negative: 2386
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000580 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2805
[LightGBM] [Info] Number of data points in the train set: 11870, number of used features: 11
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.798989 -> initscore=1.379988
[LightGBM] [Info] Start training from score 1.379988
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain

C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "


...

C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. "
C:\Users\logan\AppData\Roaming\Python\Python38\site-packages\lightgbm\engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argum

[LightGBM] [Info] Number of positive: 9484, number of negative: 2387
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000411 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2805
[LightGBM] [Info] Number of data points in the train set: 11871, number of used features: 11
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.798922 -> initscore=1.379569
[LightGBM] [Info] Start training from score 1.379569
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2023-07-07 09:56:07,347] Trial 99 finished with value: 0.5883507155217569 and parameters: {'num_leaves': 95, 'learning_rate': 0.07502002864202185, 'feature_fraction': 0.7974551062525442, 'bagging_fraction': 0.43703696519194324, 'bagging_freq': 2, 'min_child_samples': 43, 'lambda_l1': 8.837747652331837, 'lambda_l2': 5.3930123332395805}. Best is trial 55 with value: 0.5919153502570224.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

In [22]:
best_params2 = study1.best_params
best_score2 = study1.best_value

print(best_params2)
print(best_score2)

{'num_leaves': 110, 'learning_rate': 0.04925250441988242, 'feature_fraction': 0.6761209256689426, 'bagging_fraction': 0.47049346358301675, 'bagging_freq': 2, 'min_child_samples': 56, 'lambda_l1': 8.44640022445111, 'lambda_l2': 7.0108665458664685}
0.5919153502570224


In [26]:
lgb_params1 = {'num_leaves': 11, 'learning_rate': 0.05077249353326805, 'feature_fraction': 0.958792442194968,
               'bagging_fraction': 0.6562877171636153, 'bagging_freq': 4, 'min_child_samples': 32,
               'lambda_l1': 0.09118756023940255, 'lambda_l2': 8.567934907371729, 'objective': 'binary',
               'metric': 'auc', 'boosting_type': 'gbdt'}

lgb_params2 = {'num_leaves': 110, 'learning_rate': 0.04925250441988242, 'feature_fraction': 0.6761209256689426,
               'bagging_fraction': 0.47049346358301675, 'bagging_freq': 2, 'min_child_samples': 56,
               'lambda_l1': 8.44640022445111, 'lambda_l2': 7.0108665458664685,
               'objective': 'binary', 'metric': 'auc', 'boosting_type': 'gbdt'}

In [27]:
# Create a LightGBM dataset
train_data = lgb.Dataset(X_pca1, label=y)
train_data1 = lgb.Dataset(X_pca2, label=y1)

best_lgb_ec1 = lgb.train(lgb_params1, train_data, num_boost_round=1000)
best_lgb_ec2 = lgb.train(lgb_params2, train_data1, num_boost_round=1000)

[LightGBM] [Info] Number of positive: 9908, number of negative: 4930
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000256 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1530
[LightGBM] [Info] Number of data points in the train set: 14838, number of used features: 6
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.667745 -> initscore=0.698004
[LightGBM] [Info] Start training from score 0.698004
[LightGBM] [Info] Number of positive: 11855, number of negative: 2983
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000432 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2805
[LightGBM] [Info] Number of data points in the train set: 14838, number of used features: 11
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.798962 -> initscore=1.379820
[LightGBM] [Info] Start training from score 1.379820
[LightGBM] [Wa

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

In [28]:
y_pred_ec1_lgb = best_lgb_ec1.predict(test_pca1)
y_pred_ec2_lgb = best_lgb_ec2.predict(test_pca2)

In [29]:
submission_lgb = pd.DataFrame({'id': test['id'], 'EC1': y_pred_ec1_lgb, 'EC2': y_pred_ec2_lgb})
submission_lgb.to_csv('submission_lgb2.csv', index=False)

In [30]:
# Redoing Cb optuna
def objective2(trial):
    # Define the hyperparameters to optimize
    params = {
        'iterations': trial.suggest_int('iterations', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1),
        'depth': trial.suggest_int('depth', 4, 10),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 0.1, 10),
        'border_count': trial.suggest_int('border_count', 32, 255),
        'random_state': 42,
        'verbose': False
    }

    # Perform cross-validation with StratifiedKFold
    cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
    scores = []
    for train_idx, val_idx in cv.split(X_pca1, y):
        X_train, X_val = X_pca1[train_idx], X_pca1[val_idx]
        y_train, y_val = y.iloc[train_idx], y.iloc[val_idx]

        model = CatBoostClassifier(**params)
        model.fit(X_train, y_train)

        y_pred = model.predict_proba(X_val)[:, 1]
        score = roc_auc_score(y_val, y_pred)
        scores.append(score)

    # Return the mean score as the objective value for Optuna
    return np.mean(scores)

In [31]:
study2 = optuna.create_study(direction='maximize')
study2.optimize(objective2, n_trials=100)

[I 2023-07-07 10:36:00,426] A new study created in memory with name: no-name-e95ab60b-d6e1-4b15-a259-1ddfee72e7e8
[I 2023-07-07 10:36:12,757] Trial 0 finished with value: 0.6950958458251584 and parameters: {'iterations': 565, 'learning_rate': 0.03330464168962216, 'depth': 4, 'l2_leaf_reg': 4.004823507255266, 'border_count': 81}. Best is trial 0 with value: 0.6950958458251584.
[I 2023-07-07 10:36:41,177] Trial 1 finished with value: 0.6555657399635899 and parameters: {'iterations': 741, 'learning_rate': 0.0844429267848209, 'depth': 9, 'l2_leaf_reg': 9.01460428403048, 'border_count': 32}. Best is trial 0 with value: 0.6950958458251584.
[I 2023-07-07 10:37:57,563] Trial 2 finished with value: 0.678087253138745 and parameters: {'iterations': 514, 'learning_rate': 0.0446086393663451, 'depth': 10, 'l2_leaf_reg': 5.875451085798172, 'border_count': 201}. Best is trial 0 with value: 0.6950958458251584.
[I 2023-07-07 10:38:44,547] Trial 3 finished with value: 0.6491208479747057 and parameters: {

[I 2023-07-07 10:44:34,224] Trial 29 finished with value: 0.6855423279712459 and parameters: {'iterations': 556, 'learning_rate': 0.07505566071647855, 'depth': 6, 'l2_leaf_reg': 9.177415174363341, 'border_count': 238}. Best is trial 17 with value: 0.6979399216083639.
[I 2023-07-07 10:44:41,571] Trial 30 finished with value: 0.694700008194405 and parameters: {'iterations': 214, 'learning_rate': 0.07010507154141393, 'depth': 5, 'l2_leaf_reg': 8.427177655695507, 'border_count': 51}. Best is trial 17 with value: 0.6979399216083639.
[I 2023-07-07 10:44:42,842] Trial 31 finished with value: 0.6975248117204774 and parameters: {'iterations': 101, 'learning_rate': 0.05698273852667109, 'depth': 5, 'l2_leaf_reg': 9.337187127647045, 'border_count': 242}. Best is trial 17 with value: 0.6979399216083639.
[I 2023-07-07 10:44:54,506] Trial 32 finished with value: 0.6964144757325453 and parameters: {'iterations': 377, 'learning_rate': 0.05278211789160775, 'depth': 4, 'l2_leaf_reg': 8.96323174259125, 'b

[I 2023-07-07 10:48:15,284] Trial 59 finished with value: 0.6872503628565171 and parameters: {'iterations': 502, 'learning_rate': 0.09938662381918448, 'depth': 5, 'l2_leaf_reg': 6.973951240719879, 'border_count': 197}. Best is trial 40 with value: 0.6979623984906574.
[I 2023-07-07 10:48:28,141] Trial 60 finished with value: 0.6837455181781632 and parameters: {'iterations': 316, 'learning_rate': 0.09225984688712348, 'depth': 7, 'l2_leaf_reg': 7.9165600942258365, 'border_count': 183}. Best is trial 40 with value: 0.6979623984906574.
[I 2023-07-07 10:48:30,201] Trial 61 finished with value: 0.697618190576042 and parameters: {'iterations': 184, 'learning_rate': 0.08315629708301352, 'depth': 5, 'l2_leaf_reg': 9.598933492600128, 'border_count': 222}. Best is trial 40 with value: 0.6979623984906574.
[I 2023-07-07 10:48:31,405] Trial 62 finished with value: 0.6977619880787665 and parameters: {'iterations': 124, 'learning_rate': 0.0709365995810474, 'depth': 4, 'l2_leaf_reg': 9.157021017858753, 

[I 2023-07-07 10:51:20,863] Trial 89 finished with value: 0.6982333955613473 and parameters: {'iterations': 194, 'learning_rate': 0.07895248296161807, 'depth': 4, 'l2_leaf_reg': 8.055041611135884, 'border_count': 241}. Best is trial 86 with value: 0.698427289370829.
[I 2023-07-07 10:51:29,304] Trial 90 finished with value: 0.6958008495410336 and parameters: {'iterations': 274, 'learning_rate': 0.07400172357417789, 'depth': 4, 'l2_leaf_reg': 7.713772043198064, 'border_count': 241}. Best is trial 86 with value: 0.698427289370829.
[I 2023-07-07 10:51:36,347] Trial 91 finished with value: 0.6962406416527118 and parameters: {'iterations': 225, 'learning_rate': 0.08645697343446206, 'depth': 4, 'l2_leaf_reg': 7.93560412563222, 'border_count': 235}. Best is trial 86 with value: 0.698427289370829.
[I 2023-07-07 10:51:38,274] Trial 92 finished with value: 0.6976751922361547 and parameters: {'iterations': 195, 'learning_rate': 0.0787548268329235, 'depth': 4, 'l2_leaf_reg': 8.247206835928163, 'bor

In [32]:
best_params_cat1 = study2.best_params
best_score_cat1 = study2.best_value

In [34]:
def objective3(trial):
    # Define the hyperparameters to optimize
    params = {
        'iterations': trial.suggest_int('iterations', 100, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1),
        'depth': trial.suggest_int('depth', 4, 10),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 0.1, 10),
        'border_count': trial.suggest_int('border_count', 32, 255),
        'random_state': 42,
        'verbose': False
    }

    # Perform cross-validation with StratifiedKFold
    cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
    scores = []
    for train_idx, val_idx in cv.split(X_pca2, y1):
        X_train, X_val = X_pca2[train_idx], X_pca2[val_idx]
        y_train, y_val = y1.iloc[train_idx], y1.iloc[val_idx]

        model = CatBoostClassifier(**params)
        model.fit(X_train, y_train)

        y_pred = model.predict_proba(X_val)[:, 1]
        score = roc_auc_score(y_val, y_pred)
        scores.append(score)

    # Return the mean score as the objective value for Optuna
    return np.mean(scores)

In [35]:
study3 = optuna.create_study(direction='maximize')
study3.optimize(objective3, n_trials=100)

[I 2023-07-07 11:01:29,685] A new study created in memory with name: no-name-f6c23740-c6e7-4471-a76f-6c8763826a30
[I 2023-07-07 11:01:47,654] Trial 0 finished with value: 0.5628632637038246 and parameters: {'iterations': 486, 'learning_rate': 0.09672759260190314, 'depth': 6, 'l2_leaf_reg': 6.865870627543283, 'border_count': 75}. Best is trial 0 with value: 0.5628632637038246.
[I 2023-07-07 11:01:56,334] Trial 1 finished with value: 0.5809069227166596 and parameters: {'iterations': 250, 'learning_rate': 0.05254152246543666, 'depth': 5, 'l2_leaf_reg': 1.2778346983178241, 'border_count': 182}. Best is trial 1 with value: 0.5809069227166596.
[I 2023-07-07 11:02:23,570] Trial 2 finished with value: 0.5605646356076857 and parameters: {'iterations': 854, 'learning_rate': 0.09733141457287003, 'depth': 4, 'l2_leaf_reg': 8.71559926355515, 'border_count': 104}. Best is trial 1 with value: 0.5809069227166596.
[I 2023-07-07 11:02:49,878] Trial 3 finished with value: 0.576336987972309 and parameters

[I 2023-07-07 11:09:47,397] Trial 29 finished with value: 0.5750960213313925 and parameters: {'iterations': 298, 'learning_rate': 0.09970205772788632, 'depth': 5, 'l2_leaf_reg': 6.956177651660752, 'border_count': 199}. Best is trial 4 with value: 0.587764202889206.
[I 2023-07-07 11:09:58,023] Trial 30 finished with value: 0.5750833423171269 and parameters: {'iterations': 404, 'learning_rate': 0.08563862049294377, 'depth': 4, 'l2_leaf_reg': 8.049116437152048, 'border_count': 230}. Best is trial 4 with value: 0.587764202889206.
[I 2023-07-07 11:10:00,088] Trial 31 finished with value: 0.5871992523094111 and parameters: {'iterations': 172, 'learning_rate': 0.07889898441521653, 'depth': 6, 'l2_leaf_reg': 9.328657191212832, 'border_count': 65}. Best is trial 4 with value: 0.587764202889206.
[I 2023-07-07 11:10:02,349] Trial 32 finished with value: 0.5849580337239969 and parameters: {'iterations': 188, 'learning_rate': 0.09330744233093194, 'depth': 6, 'l2_leaf_reg': 9.151641570453112, 'borde

[I 2023-07-07 11:14:47,747] Trial 59 finished with value: 0.5877005126648778 and parameters: {'iterations': 141, 'learning_rate': 0.062318522680755814, 'depth': 9, 'l2_leaf_reg': 8.503425924718075, 'border_count': 119}. Best is trial 44 with value: 0.5883213182829294.
[I 2023-07-07 11:15:10,898] Trial 60 finished with value: 0.564927539369463 and parameters: {'iterations': 374, 'learning_rate': 0.06254513332158981, 'depth': 9, 'l2_leaf_reg': 8.475197300878097, 'border_count': 119}. Best is trial 44 with value: 0.5883213182829294.
[I 2023-07-07 11:15:13,176] Trial 61 finished with value: 0.5876744756659105 and parameters: {'iterations': 136, 'learning_rate': 0.0731204635935542, 'depth': 7, 'l2_leaf_reg': 7.744035140330526, 'border_count': 105}. Best is trial 44 with value: 0.5883213182829294.
[I 2023-07-07 11:15:16,423] Trial 62 finished with value: 0.5857797714442323 and parameters: {'iterations': 111, 'learning_rate': 0.07999384242163846, 'depth': 9, 'l2_leaf_reg': 8.876621760032245, 

[I 2023-07-07 11:18:31,209] Trial 89 finished with value: 0.5738115529313663 and parameters: {'iterations': 471, 'learning_rate': 0.07116394278937756, 'depth': 5, 'l2_leaf_reg': 8.1854237721932, 'border_count': 131}. Best is trial 75 with value: 0.5884914856040512.
[I 2023-07-07 11:18:43,431] Trial 90 finished with value: 0.5737953640856398 and parameters: {'iterations': 256, 'learning_rate': 0.06796148031146605, 'depth': 8, 'l2_leaf_reg': 8.979272707113639, 'border_count': 95}. Best is trial 75 with value: 0.5884914856040512.
[I 2023-07-07 11:18:45,782] Trial 91 finished with value: 0.5862383915554512 and parameters: {'iterations': 146, 'learning_rate': 0.06844130953450614, 'depth': 7, 'l2_leaf_reg': 9.46215597304219, 'border_count': 85}. Best is trial 75 with value: 0.5884914856040512.
[I 2023-07-07 11:18:47,553] Trial 92 finished with value: 0.5878413023055034 and parameters: {'iterations': 122, 'learning_rate': 0.06512245696830542, 'depth': 7, 'l2_leaf_reg': 9.767328909430733, 'bor

In [36]:
best_params_cat2 = study3.best_params
best_score_cat2 = study3.best_value

In [37]:
print(best_params_cat1)
print(best_params_cat2)

{'iterations': 177, 'learning_rate': 0.07923439815336104, 'depth': 4, 'l2_leaf_reg': 7.359695712891391, 'border_count': 255}
{'iterations': 157, 'learning_rate': 0.07872883129758723, 'depth': 8, 'l2_leaf_reg': 8.793851566280297, 'border_count': 56}


In [42]:
tuned_cat1 = {'iterations': 177, 'learning_rate': 0.07923439815336104, 'depth': 4,
              'l2_leaf_reg': 7.359695712891391, 'border_count': 255, 
              'task_type': 'GPU', 'scale_pos_weight': 0.49}
tuned_cat2 = {'iterations': 157, 'learning_rate': 0.07872883129758723, 'depth': 8,
              'l2_leaf_reg': 8.793851566280297, 'border_count': 56,
              'task_type': 'GPU', 'scale_pos_weight': 0.25}

In [ ]:
params1 = {'iterations': 162, 'task_type': 'GPU', 'scale_pos_weight': 0.49,'learning_rate': 0.021176655346253584, 
           'depth': 6, 'l2_leaf_reg': 3.362391546879058, 'border_count': 187, 'verbose': 0,
           'bagging_temperature': 0.2531663408352402, 'random_strength': 0.8864625806619271}


In [43]:
last_cat1 = cb.CatBoostClassifier(**tuned_cat1)
last_cat2 = cb.CatBoostClassifier(**tuned_cat2)

In [44]:
last_cat1.fit(X_pca1, y)
last_cat2.fit(X_pca2, y1)

last_y1 = last_cat1.predict(test_pca1)
last_y2 = last_cat2.predict(test_pca2)

0:	learn: 0.6857377	total: 4.16ms	remaining: 732ms
1:	learn: 0.6792008	total: 7.89ms	remaining: 691ms
2:	learn: 0.6733779	total: 11.2ms	remaining: 650ms
3:	learn: 0.6683391	total: 14.5ms	remaining: 628ms
4:	learn: 0.6640555	total: 16.9ms	remaining: 581ms
5:	learn: 0.6603443	total: 20.8ms	remaining: 592ms
6:	learn: 0.6570833	total: 23.7ms	remaining: 576ms
7:	learn: 0.6539350	total: 26.9ms	remaining: 569ms
8:	learn: 0.6511452	total: 29.4ms	remaining: 548ms
9:	learn: 0.6491121	total: 33.5ms	remaining: 559ms
10:	learn: 0.6470034	total: 37.2ms	remaining: 562ms
11:	learn: 0.6453364	total: 40.4ms	remaining: 555ms
12:	learn: 0.6436503	total: 44ms	remaining: 555ms
13:	learn: 0.6422725	total: 47.4ms	remaining: 552ms
14:	learn: 0.6408254	total: 51.3ms	remaining: 554ms
15:	learn: 0.6396058	total: 54.8ms	remaining: 552ms
16:	learn: 0.6384669	total: 59.4ms	remaining: 559ms
17:	learn: 0.6374467	total: 62.8ms	remaining: 555ms
18:	learn: 0.6365295	total: 65.6ms	remaining: 545ms
19:	learn: 0.6358521	tot

0:	learn: 0.6912959	total: 7.23ms	remaining: 1.13s
1:	learn: 0.6897001	total: 13.3ms	remaining: 1.03s
2:	learn: 0.6881487	total: 18.9ms	remaining: 969ms
3:	learn: 0.6866914	total: 24.3ms	remaining: 928ms
4:	learn: 0.6854304	total: 30.6ms	remaining: 931ms
5:	learn: 0.6839814	total: 36ms	remaining: 905ms
6:	learn: 0.6826138	total: 42ms	remaining: 900ms
7:	learn: 0.6814654	total: 47.1ms	remaining: 877ms
8:	learn: 0.6804831	total: 52.7ms	remaining: 867ms
9:	learn: 0.6795533	total: 58.3ms	remaining: 858ms
10:	learn: 0.6786177	total: 64.3ms	remaining: 854ms
11:	learn: 0.6778083	total: 69.7ms	remaining: 842ms
12:	learn: 0.6771825	total: 75.4ms	remaining: 835ms
13:	learn: 0.6765683	total: 81.9ms	remaining: 836ms
14:	learn: 0.6756821	total: 87.3ms	remaining: 826ms
15:	learn: 0.6747619	total: 93.4ms	remaining: 823ms
16:	learn: 0.6738677	total: 101ms	remaining: 829ms
17:	learn: 0.6730760	total: 107ms	remaining: 825ms
18:	learn: 0.6725337	total: 111ms	remaining: 805ms
19:	learn: 0.6719872	total: 1

In [45]:
submission_last = pd.DataFrame({'id': test['id'], 'EC1': last_y1, 'EC2': last_y2})
submission_last.to_csv('submission_last_weight.csv', index=False)

Out of all the model versions trained, the first one which was trained using only the original data without transforming somehow proved to be the most accurate. It is worth mentioning that the approach taken for this solution was not to make a single multilable model but to train a model for each needed prediction. Using this method allowed the data to be transformed differently for each model and achieve a better preforming score.